# Natural language image search with a Dual Encoder

**Authors:** [Leo Pimentel](https://www.linkedin.com/in/leo-pimentel),[Nitesh Chinthireddy](),[Rathi Anand]()<br>
**Date created:** 2024/03/29<br>
**Last modified:** 2024/05/13<br>
**Description:** Implementation of a dual encoder model for retrieving images that match natural language queries.<br>
**Credits** Khalid Salama for earlier work


## Introduction

The example demonstrates how to build a dual encoder neural network
model to search for images using natural language. The model is inspired by
the [CLIP](https://openai.com/blog/clip/)
approach, introduced by Alec Radford et al. The idea is to train a vision encoder and a text
encoder jointly to project the representation of images and their captions into the same embedding
space, such that the caption embeddings are located near the embeddings of the images they describe.
To compensate for a heavily reduced AMZN bin dataset, data augmentation from Albumentations generated
9 additional samples per image; increased the number of entries from 10144 to 101,444.

This example requires TensorFlow 2.15.post1.
In addition, [TensorFlow Hub](https://www.tensorflow.org/hub)
and [TensorFlow Text](https://www.tensorflow.org/tutorials/tensorflow_text/intro)
are required for the BERT model, and TF 2.15.post1
is required for the AdamW optimizer. These libraries can be installed using the
following command:

```python
pip install -q -U tensorflow==2.15.* tensorflow-hub tensorflow-text==2.15.*
```


## Setup


In [54]:
# Uninstall tensorflow installed by conda, to avoid dependency issues with hub and text modules
# conda remove tensorflow=2.15
# !pip install -q -U tensorflow==2.15.* tensorflow-hub tensorflow-text==2.15.*

In [55]:
# !pip show tensorflow tensorflow-hub tensorflow-text keras numpy

In [7]:
import os
import collections
import json
import numpy as np
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
import tensorflow_hub as hub
import tensorflow_text as text
import fiftyone as fo
from pathlib import Path

# import tensorflow_addons as tfa
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
from tqdm import tqdm
import pdb

# Suppressing tf.hub warnings
tf.get_logger().setLevel("ERROR")
print(f"Number of GPUs: {len(tf.config.list_physical_devices('GPU'))}")

2024-05-13 02:33:48.238394: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


Number of GPUs: 0


## Prepare the data

We will use a pretrained models for Xception and Bert. The Ik datasst was
reviewed in various notebooks and organized into processed_df.csv.  
Microsoft's Data Wrangler, the preferred data wranglineg tool in VSCode, supports
the various methods to evaluate the datsets from class (product_id) grouping to
FiftyOne Visualization tool.
"final_project/notebooks/ikdataset_analysis.ipynb"

###

Download and extract the data

First, let's download the dataset, which consists of two compressed folders:
one with images, and the other—with associated image captions.
Note that the compressed images folder is 13GB in size.


In [57]:
import os
import pandas as pd

root_dir = "datasets"
mapped_dir = os.path.join(".", root_dir, "mapped")
amzn_bin_df = pd.read_csv(os.path.join(mapped_dir, "processed_df.csv"), dtype={"image_name": str})
amzn_bin_df.head()

image_name  EXPECTED_QUANTITY      asin_1  height_1  length_1  \
0      00015                 15  B0033UNIQC       0.7      10.5   
1      00016                 12  B0033UNIQC       0.7      10.5   
2      00017                 10  B0033UNIQC       0.7      10.5   
3      00037                  3  B00F908YU4       4.0       5.8   
4      00038                  2  B00F908YU4       4.0       5.8   

                                              name_1  \
0  Fiskars 8 Inch Premier Softgrip Titanium Strai...   
1  Fiskars 8 Inch Premier Softgrip Titanium Strai...   
2  Fiskars 8 Inch Premier Softgrip Titanium Strai...   
3  12Watt 4-inch High CRI Wet Location Dimmable R...   
4  12Watt 4-inch High CRI Wet Location Dimmable R...   

                                    normalizedName_1  quantity_1  weight_1  \
0  Fiskars 8 Inch Premier Softgrip Titanium Strai...          14       0.2   
1  Fiskars 8 Inch Premier Softgrip Titanium Strai...          11       0.2   
2  Fiskars 8 Inch Premier Softgrip Titanium Strai...           9       0.2   
3  12Watt 4-inch High CRI Wet Location Dimmable R...           1       0.7   
4  12Watt 4-inch High CRI Wet Location Dimmable R...           1       0.7   

   width_1  ... weight_3  width_3  asin_4 height_4 length_4  name_4  \
0      4.0  ...      NaN      NaN     NaN      NaN      NaN     NaN   
1      4.0  ...      NaN      NaN     NaN      NaN      NaN     NaN   
2      4.0  ...      NaN      NaN     NaN      NaN      NaN     NaN   
3      5.7  ...      0.4      4.0     NaN      NaN      NaN     NaN   
4      5.7  ...      NaN      NaN     NaN      NaN      NaN     NaN   

   normalizedName_4  quantity_4 weight_4  width_4  
0               NaN         NaN      NaN      NaN  
1               NaN         NaN      NaN      NaN  
2               NaN         NaN      NaN      NaN  
3               NaN         NaN      NaN      NaN  
4               NaN         NaN      NaN      NaN  

[5 rows x 34 columns]

In [58]:
"""
Transform the Proceessed.CSV (the original IK dataset) from a 34-column to a 3-column table, 
using a pivot(melt) method each product_id is listed separately in a row with the corresponding image_id and caption.

fieldnames = [
    "image_name",
    "EXPECTED_QUANTITY",
    "asin_1",
    "height_1",
    "length_1",
    "name_1",
    "normalizedName_1",
    "quantity_1",
    "weight_1",
    "width_1",
    "asin_2",
    "height_2",
    "length_2",
    "name_2",
    "normalizedName_2",
    "quantity_2",
    "weight_2",
    "width_2",
    "asin_3",
    "height_3",
    "length_3",
    "name_3",
    "normalizedName_3",
    "quantity_3",
    "weight_3",
    "width_3",
    "asin_4",
    "height_4",
    "length_4",
    "name_4",
    "normalizedName_4",
    "quantity_4",
    "weight_4",
    "width_4",
]
"""

# Drop unnecessary columns
cols_to_drop = [
    col
    for col in amzn_bin_df.columns
    if "weight" in col or "width" in col or "height" in col or "length" in col or "name_" in col
]
amzn_bin_df = amzn_bin_df.drop(columns=cols_to_drop)

# Define the base fields for melting
base_fields = ["image_name", "EXPECTED_QUANTITY"]

# Melt the DataFrame to unpivot it, focusing on the image_name and product-related columns
df_long = pd.melt(amzn_bin_df, id_vars=base_fields, var_name="variable", value_name="value")

# Extract numeric suffix from variable names to identify the product instance
df_long["id_num"] = df_long["variable"].str.extract("(\d+)$")  # Extract numeric suffix
df_long["variable_base"] = df_long["variable"].str.replace("_\d+$", "")  # Remove numeric suffix

# Pivot the table back to a wide format, now with each product instance in a separate row
df_wide = df_long.pivot_table(index=["image_name", "id_num"], columns="variable_base", values="value", aggfunc="first")

# Reset the index to turn MultiIndex into columns
df_wide.reset_index(inplace=True)

# Generate a new DataFrame with the desired dictionary structure
# Updated list of dictionaries creation using df_wide DataFrame structure
list_of_dicts = df_wide.apply(
    lambda row: {
        "image_id": row["image_name"].replace(".json", ".jpg"),  # Convert .json to .jpg
        "id": row.get(f'asin_{row["id_num"]}', "No ASIN"),  # Use ASIN corresponding to id_num
        "caption": ",".join(
            [
                str(row.get(f'asin_{row["id_num"]}', "No ASIN")),
                str(row.get(f'normalizedName_{row["id_num"]}', "No description")),
                str(row.get(f'quantity_{row["id_num"]}', "0")),  # Default to '0' if quantity is not available
            ]
        ),
    },
    axis=1,
).tolist()

# Print to check output
print(list_of_dicts[:5])  # Print the first 5 entries to check
print("Length of list: ", len(list_of_dicts))

[{'image_id': '00015', 'id': 'B0033UNIQC', 'caption': 'B0033UNIQC,Fiskars 8 Inch Premier Softgrip Titanium Straight Scissors (01-004244J),14'}, {'image_id': '00015', 'id': 'B00E9J3MLM', 'caption': 'B00E9J3MLM,Kitchen Safe: Time Locking Container (White Lid + Clear Base) - 5.5" Height,1.0'}, {'image_id': '00016', 'id': 'B0033UNIQC', 'caption': 'B0033UNIQC,Fiskars 8 Inch Premier Softgrip Titanium Straight Scissors (01-004244J),11'}, {'image_id': '00016', 'id': 'B00E9J3MLM', 'caption': 'B00E9J3MLM,Kitchen Safe: Time Locking Container (White Lid + Clear Base) - 5.5" Height,1.0'}, {'image_id': '00017', 'id': 'B0033UNIQC', 'caption': 'B0033UNIQC,Fiskars 8 Inch Premier Softgrip Titanium Straight Scissors (01-004244J),9'}]
Length of list:  10144


In [59]:
amzn_bin_df = pd.DataFrame(list_of_dicts)
amzn_bin_df.name = "IK_binsense"

In [60]:
# Synthetic image creations with albumentations
import albumentations as A
import cv2

image_names = amzn_bin_df["image_id"].values
curr_dir = Path.cwd()
images_dir = Path(curr_dir / "./datasets/aft-vbi-pds/bin-images")
NUM_OF_SYN_IMG = 10
# Iterate over the images
complete = {}
for image in image_names:
    if not image in complete:
        # Execute if image was not processed.
        complete[image] = True
        for iter in range(1, NUM_OF_SYN_IMG):
            new_image = image + ".jpg"
            new_image = os.path.join(images_dir, new_image)
            img = cv2.imread(new_image)
            img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
            # Apply transformations
            transform = A.Compose(
                [
                    A.Sharpen(alpha=(0.2, 0.5), p=0.75),
                    A.HorizontalFlip(p=0.5),
                    A.RandomBrightnessContrast(p=0.2),
                ]
            )
            transformed = transform(image=img)
            transformed_image = transformed["image"]
            new_image = new_image.split("/")[-1]
            new_image = os.path.join(images_dir, new_image.replace(".jpg", "_" + str(iter) + ".jpg"))
            # Save the image and overwrite if filename exists!
            # There should be only 6 iterations per image containing multiple products.
            cv2.imwrite(new_image, cv2.cvtColor(transformed_image, cv2.COLOR_RGB2BGR))

# Create new entries in the DataFrame for the synthetic images
# The image_id will be updated to include the iteration number
# The rest of the row values will be the same
# The image id will contain duplicates if the image has multiple products in the original image.
rows_to_append = []
for row in amzn_bin_df.iterrows():
    row = row[1]
    for iter in range(1, NUM_OF_SYN_IMG):
        a_row = {}
        new_image = row["image_id"] + "_" + str(iter)
        a_row["image_id"] = new_image
        # Update a_row dictionary with the rest of the row values
        a_row |= row[1:].to_dict()
        # Append to the list of dictionaries
        rows_to_append.append(a_row)

# Concat the old DataFrame with the updated list of dictionaries
amzn_bin_df = pd.concat([amzn_bin_df, pd.DataFrame(rows_to_append)], ignore_index=True)
amzn_bin_df.head()
amzn_bin_df

image_id          id  \
0          00015  B0033UNIQC   
1          00015  B00E9J3MLM   
2          00016  B0033UNIQC   
3          00016  B00E9J3MLM   
4          00017  B0033UNIQC   
...          ...         ...   
101435  114395_5  B00L3PZF56   
101436  114395_6  B00L3PZF56   
101437  114395_7  B00L3PZF56   
101438  114395_8  B00L3PZF56   
101439  114395_9  B00L3PZF56   

                                                  caption  
0       B0033UNIQC,Fiskars 8 Inch Premier Softgrip Tit...  
1       B00E9J3MLM,Kitchen Safe: Time Locking Containe...  
2       B0033UNIQC,Fiskars 8 Inch Premier Softgrip Tit...  
3       B00E9J3MLM,Kitchen Safe: Time Locking Containe...  
4       B0033UNIQC,Fiskars 8 Inch Premier Softgrip Tit...  
...                                                   ...  
101435  B00L3PZF56,Sakkas 12311 Fairy Maiden Corset St...  
101436  B00L3PZF56,Sakkas 12311 Fairy Maiden Corset St...  
101437  B00L3PZF56,Sakkas 12311 Fairy Maiden Corset St...  
101438  B00L3PZF56,Sakkas 12311 Fairy Maiden Corset St...  
101439  B00L3PZF56,Sakkas 12311 Fairy Maiden Corset St...  

[101440 rows x 3 columns]

In [61]:
amzn_bin_df.to_csv(os.path.join(mapped_dir, "image_caption.csv"), index=False)

In [62]:
# Convert into JSON
list_of_dicts = amzn_bin_df.to_dict(orient="records")
target_dict = {"annotations": list_of_dicts}
annotations_dir = os.path.join(root_dir, "annotations")
# Create an ASIN.json file to create TF Records.
target_file = os.path.join(annotations_dir, "asin.json")
# File name is asin.json
with open(target_file, "w") as f:
    json.dump(target_dict, f)

In [63]:
root_dir = "datasets"
annotations_dir = os.path.join(root_dir, "annotations")
# images_dir = "/Users/leonardpimentel/Downloads/kaggle/datasets/aft-vbi-pds/bin-images"
tfrecords_dir = os.path.join(root_dir, "tfrecords")
annotation_file = os.path.join(annotations_dir, "asin.json")
"""
# Download caption annotation files
if not os.path.exists(annotations_dir):
    annotation_zip = keras.utils.get_file(
        "captions.zip",
        cache_dir=os.path.abspath("."),
        origin="http://images.cocodataset.org/annotations/annotations_trainval2014.zip",
        extract=True,
    )
    os.remove(annotation_zip)

# Download image files
if not os.path.exists(images_dir):
    image_zip = keras.utils.get_file(
        "train2014.zip",
        cache_dir=os.path.abspath("."),
        origin="http://images.cocodataset.org/zips/train2014.zip",
        extract=True,
    )
    os.remove(image_zip)

"""

print("Dataset is downloaded and extracted successfully.")

with open(annotation_file, "r") as f:
    annotations = json.load(f)["annotations"]

image_path_to_caption = collections.defaultdict(list)
for element in annotations:
    caption = f"{element['caption'].lower().rstrip('.')}"
    # image_path = images_dir + "/COCO_train2014_" + "%012d.jpg" % (element["image_id"])
    image_path = os.path.join(images_dir, "%s.jpg" % (element["image_id"]))
    image_path_to_caption[image_path].append(caption)

image_paths = list(image_path_to_caption.keys())
print(f"Number of images: {len(image_paths)}")

Dataset is downloaded and extracted successfully.
Number of images: 38750


In [64]:
print(image_path_to_caption[image_paths[0]])

['b0033uniqc,fiskars 8 inch premier softgrip titanium straight scissors (01-004244j),14', 'b00e9j3mlm,kitchen safe: time locking container (white lid + clear base) - 5.5" height,1.0']


In [65]:
#
print(image_paths)
print(image_path_to_caption.keys())

['/home/ubuntu/ml/final_project/notebooks/datasets/aft-vbi-pds/bin-images/00015.jpg', '/home/ubuntu/ml/final_project/notebooks/datasets/aft-vbi-pds/bin-images/00016.jpg', '/home/ubuntu/ml/final_project/notebooks/datasets/aft-vbi-pds/bin-images/00017.jpg', '/home/ubuntu/ml/final_project/notebooks/datasets/aft-vbi-pds/bin-images/00037.jpg', '/home/ubuntu/ml/final_project/notebooks/datasets/aft-vbi-pds/bin-images/00038.jpg', '/home/ubuntu/ml/final_project/notebooks/datasets/aft-vbi-pds/bin-images/00049.jpg', '/home/ubuntu/ml/final_project/notebooks/datasets/aft-vbi-pds/bin-images/00050.jpg', '/home/ubuntu/ml/final_project/notebooks/datasets/aft-vbi-pds/bin-images/00079.jpg', '/home/ubuntu/ml/final_project/notebooks/datasets/aft-vbi-pds/bin-images/00080.jpg', '/home/ubuntu/ml/final_project/notebooks/datasets/aft-vbi-pds/bin-images/00081.jpg', '/home/ubuntu/ml/final_project/notebooks/datasets/aft-vbi-pds/bin-images/00084.jpg', '/home/ubuntu/ml/final_project/notebooks/datasets/aft-vbi-pds/bi

### Process and save the data to TFRecord files

You can change the `sample_size` parameter to control many image-caption pairs
will be used for training the dual encoder model.
In this example we set `train_size` to 30,000 images,
which is about 35% of the dataset. We use 2 captions for each
image, thus producing 60,000 image-caption pairs. The size of the training set
affects the quality of the produced encoders, but more examples would lead to
longer training time.


In [84]:
train_size = 30000
valid_size = 5000
captions_per_image = 4
images_per_file = 2000

train_image_paths = image_paths[:train_size]
num_train_files = int(np.ceil(train_size / images_per_file))
train_files_prefix = os.path.join(tfrecords_dir, "train")

valid_image_paths = image_paths[-valid_size:]
num_valid_files = int(np.ceil(valid_size / images_per_file))
valid_files_prefix = os.path.join(tfrecords_dir, "valid")

tf.io.gfile.makedirs(tfrecords_dir)


def bytes_feature(value):
    return tf.train.Feature(bytes_list=tf.train.BytesList(value=[value]))


def create_example(image_path, caption):
    feature = {
        "caption": bytes_feature(caption.encode()),
        "raw_image": bytes_feature(tf.io.read_file(image_path).numpy()),
    }
    return tf.train.Example(features=tf.train.Features(feature=feature))


def write_tfrecords(file_name, image_paths):
    caption_list = []
    image_path_list = []
    for image_path in image_paths:
        captions = image_path_to_caption[image_path][:captions_per_image]
        caption_list.extend(captions)
        image_path_list.extend([image_path] * len(captions))

    with tf.io.TFRecordWriter(file_name) as writer:
        for example_idx in range(len(image_path_list)):
            example = create_example(image_path_list[example_idx], caption_list[example_idx])
            writer.write(example.SerializeToString())
    return example_idx + 1


def write_data(image_paths, num_files, files_prefix):
    example_counter = 0
    for file_idx in tqdm(range(num_files)):
        file_name = files_prefix + "-%02d.tfrecord" % (file_idx)
        start_idx = images_per_file * file_idx
        end_idx = start_idx + images_per_file
        example_counter += write_tfrecords(file_name, image_paths[start_idx:end_idx])
    return example_counter


train_example_count = write_data(train_image_paths, num_train_files, train_files_prefix)
print(f"{train_example_count} training examples were written to tfrecord files.")

valid_example_count = write_data(valid_image_paths, num_valid_files, valid_files_prefix)
print(f"{valid_example_count} evaluation examples were written to tfrecord files.")

100%|██████████| 15/15 [01:21<00:00,  5.41s/it]


78475 training examples were written to tfrecord files.


100%|██████████| 3/3 [00:13<00:00,  4.63s/it]

13259 evaluation examples were written to tfrecord files.


### Create `tf.data.Dataset` for training and evaluation


In [85]:
feature_description = {
    "caption": tf.io.FixedLenFeature([], tf.string),
    "raw_image": tf.io.FixedLenFeature([], tf.string),
}


def read_example(example):
    features = tf.io.parse_single_example(example, feature_description)
    raw_image = features.pop("raw_image")
    features["image"] = tf.image.resize(tf.image.decode_jpeg(raw_image, channels=3), size=(299, 299))
    return features


def get_dataset(file_pattern, batch_size):

    return (
        tf.data.TFRecordDataset(tf.data.Dataset.list_files(file_pattern))
        .map(
            read_example,
            num_parallel_calls=tf.data.AUTOTUNE,
            deterministic=False,
        )
        .shuffle(batch_size * 10)
        .prefetch(buffer_size=tf.data.AUTOTUNE)
        .batch(batch_size)
    )

## Implement the projection head

The projection head is used to transform the image and the text embeddings to
the same embedding space with the same dimensionality.


In [86]:
def project_embeddings(embeddings, num_projection_layers, projection_dims, dropout_rate):
    # Use gelu activations within keras
    projected_embeddings = layers.Dense(units=projection_dims, activation=tf.nn.gelu)(embeddings)
    for _ in range(num_projection_layers):
        # x = tf.nn.gelu(projected_embeddings)
        x = layers.Dense(projection_dims, activation=tf.nn.gelu)(projected_embeddings)
        x = layers.Dropout(dropout_rate)(x)
        x = layers.Add()([projected_embeddings, x])
        # Layer normalization
        projected_embeddings = layers.LayerNormalization()(x)
    return projected_embeddings

## Implement the vision encoder

In this example, we use [Xception](https://keras.io/api/applications/xception/)
from [Keras Applications](https://keras.io/api/applications/) as the base for the
vision encoder.


In [87]:
def create_vision_encoder(num_projection_layers, projection_dims, dropout_rate, trainable=False):
    # Load the pre-trained Xception model to be used as the base encoder.
    xception = keras.applications.Xception(include_top=False, weights="imagenet", pooling="avg")
    # Set the trainability of the base encoder.
    for layer in xception.layers:
        layer.trainable = trainable
    # Receive the images as inputs.
    inputs = layers.Input(shape=(299, 299, 3), name="image_input")

    # Preprocess the input image.
    xception_input = keras.applications.xception.preprocess_input(inputs)
    # Generate the embeddings for the images using the xception model.
    embeddings = xception(xception_input)
    # Project the embeddings produced by the model.
    outputs = project_embeddings(embeddings, num_projection_layers, projection_dims, dropout_rate)
    # Create the vision encoder model.
    return keras.Model(inputs, outputs, name="vision_encoder")

## Implement the text encoder

We use [BERT](https://tfhub.dev/tensorflow/small_bert/bert_en_uncased_L-12_H-256_A-4/1)
from [TensorFlow Hub](https://tfhub.dev) as the text encoder


In [88]:
def create_text_encoder(num_projection_layers, projection_dims, dropout_rate, trainable=False):
    # Load the BERT preprocessing module.
    preprocess = hub.KerasLayer(
        "https://tfhub.dev/tensorflow/bert_en_uncased_preprocess/3",
        name="text_preprocessing",
    )
    # Load the pre-trained BERT model to be used as the base encoder.
    # Set the trainability of the base encoder.
    bert = hub.KerasLayer(
        "https://tfhub.dev/tensorflow/small_bert/bert_en_uncased_L-4_H-512_A-8/1",
        trainable=trainable,
        name="bert",
    )
    # Receive the text as inputs.
    inputs = layers.Input(shape=(), dtype=tf.string, name="text_input")
    # Preprocess the text.
    bert_inputs = preprocess(inputs)
    # Generate embeddings for the preprocessed text using the BERT model.
    embeddings = bert(bert_inputs)["pooled_output"]
    # Project the embeddings produced by the model.
    outputs = project_embeddings(embeddings, num_projection_layers, projection_dims, dropout_rate)
    # Create the text encoder model.
    return keras.Model(inputs, outputs, name="text_encoder")

## Implement the dual encoder

To calculate the loss, we compute the pairwise dot-product similarity between
each `caption_i` and `images_j` in the batch as the predictions.
The target similarity between `caption_i` and `image_j` is computed as
the average of the (dot-product similarity between `caption_i` and `caption_j`)
and (the dot-product similarity between `image_i` and `image_j`).
Then, we use crossentropy to compute the loss between the targets and the predictions.


In [89]:
class DualEncoder(keras.Model):
    def __init__(self, text_encoder, vision_encoder, temperature=1.0, **kwargs):
        super().__init__(**kwargs)
        self.text_encoder = text_encoder
        self.vision_encoder = vision_encoder
        self.temperature = temperature
        self.loss_tracker = keras.metrics.Mean(name="loss")

    @property
    def metrics(self):
        return [self.loss_tracker]

    def call(self, features, training=False):
        # Place each encoder on a separate GPU (if available).
        # TF will fallback on available devices if there are fewer than 2 GPUs.
        with tf.device("/gpu:0"):
            # Get the embeddings for the captions.
            caption_embeddings = self.text_encoder(features["caption"], training=training)
        with tf.device("/gpu:1"):
            # Get the embeddings for the images.
            image_embeddings = self.vision_encoder(features["image"], training=training)
        return caption_embeddings, image_embeddings

    def compute_loss(self, caption_embeddings, image_embeddings):
        # logits[i][j] is the dot_similarity(caption_i, image_j).
        logits = tf.matmul(caption_embeddings, image_embeddings, transpose_b=True) / self.temperature
        # images_similarity[i][j] is the dot_similarity(image_i, image_j).
        images_similarity = tf.matmul(image_embeddings, image_embeddings, transpose_b=True)
        # captions_similarity[i][j] is the dot_similarity(caption_i, caption_j).
        captions_similarity = tf.matmul(caption_embeddings, caption_embeddings, transpose_b=True)
        # targets[i][j] = avarage dot_similarity(caption_i, caption_j) and dot_similarity(image_i, image_j).
        targets = keras.activations.softmax((captions_similarity + images_similarity) / (2 * self.temperature))
        # Compute the loss for the captions using crossentropy
        captions_loss = keras.losses.categorical_crossentropy(y_true=targets, y_pred=logits, from_logits=True)
        # Compute the loss for the images using crossentropy
        images_loss = keras.losses.categorical_crossentropy(
            y_true=tf.transpose(targets), y_pred=tf.transpose(logits), from_logits=True
        )
        # Return the mean of the loss over the batch.
        return (captions_loss + images_loss) / 2

    def train_step(self, features):
        with tf.GradientTape() as tape:
            # Forward pass
            caption_embeddings, image_embeddings = self(features, training=True)
            loss = self.compute_loss(caption_embeddings, image_embeddings)
        # Backward pass
        gradients = tape.gradient(loss, self.trainable_variables)
        self.optimizer.apply_gradients(zip(gradients, self.trainable_variables))
        # Monitor loss
        self.loss_tracker.update_state(loss)
        return {"loss": self.loss_tracker.result()}

    def test_step(self, features):
        caption_embeddings, image_embeddings = self(features, training=False)
        loss = self.compute_loss(caption_embeddings, image_embeddings)
        self.loss_tracker.update_state(loss)
        return {"loss": self.loss_tracker.result()}

## Train the dual encoder model

In this experiment, we freeze the base encoders for text and images, and make only
the projection head trainable.


In [90]:
num_epochs = 40  # In practice, train for at least 30 epochs
batch_size = 256
# %debug
vision_encoder = create_vision_encoder(num_projection_layers=1, projection_dims=256, dropout_rate=0.1)
text_encoder = create_text_encoder(num_projection_layers=1, projection_dims=256, dropout_rate=0.1)
dual_encoder = DualEncoder(text_encoder, vision_encoder, temperature=0.05)
dual_encoder.compile(optimizer=keras.optimizers.AdamW(learning_rate=0.001, weight_decay=0.001))

Note that training the model with 60,000 image-caption pairs, with a batch size of 256,
takes around 12 minutes per epoch using a V100 GPU accelerator. If 2 GPUs are available,
the epoch takes around 8 minutes.


In [91]:
print(f"Number of GPUs: {len(tf.config.list_physical_devices('GPU'))}")
print(f"Number of examples (caption-image pairs): {train_example_count}")
print(f"Batch size: {batch_size}")
print(f"Steps per epoch: {int(np.ceil(train_example_count / batch_size))}")
train_dataset = get_dataset(os.path.join(tfrecords_dir, "train-*.tfrecord"), batch_size)
valid_dataset = get_dataset(os.path.join(tfrecords_dir, "valid-*.tfrecord"), batch_size)
# Create a learning rate scheduler callback.
reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor="val_loss", factor=0.2, patience=3)
# Create an early stopping callback.
early_stopping = keras.callbacks.EarlyStopping(monitor="val_loss", patience=5, restore_best_weights=True)
history = dual_encoder.fit(
    train_dataset,
    epochs=num_epochs,
    validation_data=valid_dataset,
    callbacks=[reduce_lr, early_stopping],
)
print("Training completed. Saving vision and text encoders...")
# Keras recommends .keras
"""
A Keras model consists of multiple components:

The architecture, or configuration, which specifies what layers the model contain, and how they're connected.
A set of weights values (the "state of the model").
An optimizer (defined by compiling the model).
A set of losses and metrics (defined by compiling the model).
The Keras API saves all of these pieces together in a unified format, marked by the .keras extension. This is a zip archive consisting of the following:

A JSON-based configuration file (config.json): Records of model, layer, and other trackables' configuration.
A H5-based state file, such as model.weights.h5 (for the whole model), with directory keys for layers and their weights.
A metadata file in JSON, storing things such as the current Keras version.

"""
vision_encoder.save("vision_encoder_final.keras")
text_encoder.save("text_encoder_final.keras")
print("Models are saved in Keras 3.")

Number of GPUs: 1
Number of examples (caption-image pairs): 78475
Batch size: 256
Steps per epoch: 307
Epoch 1/40
    325/Unknown - 1135s 3s/step - loss: 39.4983

2024-05-13 02:08:46.942710: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 11915701575385399194
2024-05-13 02:08:46.942774: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 13431616764581691750
2024-05-13 02:08:46.942792: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 10491237912913260872
2024-05-13 02:08:46.942806: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 11435426201425935910
2024-05-13 02:08:46.942823: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 7570063115187808069
2024-05-13 02:08:46.942843: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous recv item cancelled. Key hash: 12404762873676587737
2024-05-13 02:08:46.942856: I tensorflow/core/framework/local_rendezvous.cc:421] Local rendezvous rec

325/325 [==============================] - 1339s 4s/step - loss: 39.4983 - val_loss: 6.8324 - lr: 0.0010
Epoch 2/40
325/325 [==============================] - 1309s 4s/step - loss: 6.4549 - val_loss: 5.8227 - lr: 0.0010
Epoch 3/40
325/325 [==============================] - 1314s 4s/step - loss: 5.9249 - val_loss: 5.7044 - lr: 0.0010
Epoch 4/40
325/325 [==============================] - 1307s 4s/step - loss: 5.7580 - val_loss: 5.6417 - lr: 0.0010
Epoch 5/40
325/325 [==============================] - 1307s 4s/step - loss: 5.6572 - val_loss: 5.6201 - lr: 0.0010
Epoch 6/40
325/325 [==============================] - 1309s 4s/step - loss: 5.5664 - val_loss: 5.6129 - lr: 0.0010
Epoch 7/40
325/325 [==============================] - 1331s 4s/step - loss: 5.4829 - val_loss: 5.6196 - lr: 0.0010
Epoch 8/40
325/325 [==============================] - 1318s 4s/step - loss: 5.3892 - val_loss: 5.6225 - lr: 0.0010
Epoch 9/40
325/325 [==============================] - 1310s 4s/step - loss: 5.2794 - val_l

In [92]:
vision_encoder.save("vision_encoder_final")
text_encoder.save("text_encoder_final")
print("Models are saved in Keras 2.")

Models are saved in Keras 2.


Plotting the training loss:


In [93]:
plt.plot(history.history["loss"])
plt.plot(history.history["val_loss"])
plt.ylabel("Loss")
plt.xlabel("Epoch")
plt.legend(["train", "valid"], loc="upper right")
plt.show()

## Search for images using natural language queries

We can then retrieve images corresponding to natural language queries via
the following steps:

1. Generate embeddings for the images by feeding them into the `vision_encoder`.
2. Feed the natural language query to the `text_encoder` to generate a query embedding.
3. Compute the similarity between the query embedding and the image embeddings
   in the index to retrieve the indices of the top matches.
4. Look up the paths of the top matching images to display them.

Note that, after training the `dual encoder`, only the fine-tuned `vision_encoder`
and `text_encoder` models will be used, while the `dual_encoder` model will be discarded.


### Generate embeddings for the images

We load the images and feed them into the `vision_encoder` to generate their embeddings.
In large scale systems, this step is performed using a parallel data processing framework,
such as [Apache Spark](https://spark.apache.org) or [Apache Beam](https://beam.apache.org).
Generating the image embeddings may take several minutes.


In [ ]:
print("Loading vision and text encoders...")
vision_encoder = keras.models.load_model("vision_encoder")
text_encoder = keras.models.load_model("text_encoder")
print("Models are loaded.")


def read_image(image_path):
    image_array = tf.image.decode_jpeg(tf.io.read_file(image_path), channels=3)
    return tf.image.resize(image_array, (299, 299))


print(f"Generating embeddings for {len(image_paths)} images...")
image_embeddings = vision_encoder.predict(
    tf.data.Dataset.from_tensor_slices(image_paths).map(read_image).batch(batch_size),
    verbose=1,
)
print(f"Image embeddings shape: {image_embeddings.shape}.")

### Retrieve relevant images

In this example, we use exact matching by computing the dot product similarity
between the input query embedding and the image embeddings, and retrieve the top k
matches. However, _approximate_ similarity matching, using frameworks like
[ScaNN](https://github.com/google-research/google-research/tree/master/scann),
[Annoy](https://github.com/spotify/annoy), or [Faiss](https://github.com/facebookresearch/faiss)
is preferred in real-time use cases to scale with a large number of images.


In [3]:
def find_matches(image_embeddings, queries, k=9, normalize=True):
    # Get the embedding for the query.
    query_embedding = text_encoder(tf.convert_to_tensor(queries))
    # Normalize the query and the image embeddings.
    if normalize:
        image_embeddings = tf.math.l2_normalize(image_embeddings, axis=1)
        query_embedding = tf.math.l2_normalize(query_embedding, axis=1)
    # Compute the dot product between the query and the image embeddings.
    dot_similarity = tf.matmul(query_embedding, image_embeddings, transpose_b=True)
    # Retrieve top k indices.
    results = tf.math.top_k(dot_similarity, k).indices.numpy()
    # Return matching image paths.
    return [[image_paths[idx] for idx in indices] for indices in results]

Set the `query` variable to the type of images you want to search for.
Try things like: 'a plate of healthy food',
'a woman wearing a hat is walking down a sidewalk',
'a bird sits near to the water', or 'wild animals are standing in a field'.


In [ ]:
# query = "a family standing next to the ocean on a sandy beach with a surf board"
query = "Fiskars 8 Inch Premier Softgrip Titanium Straight Scissors (01-004244J)"  # "Titanium Straight Scissors"
matches = find_matches(image_embeddings, [query], normalize=True)[0]
print(matches)

plt.figure(figsize=(20, 20))
for i in range(9):
    ax = plt.subplot(3, 3, i + 1)
    plt.imshow(mpimg.imread(matches[i]))
    plt.axis("off")

## Evaluate the retrieval quality

To evaluate the dual encoder model, we use the captions as queries.
We use the out-of-training-sample images and captions to evaluate the retrieval quality,
using top k accuracy. A true prediction is counted if, for a given caption, its associated image
is retrieved within the top k matches.


In [97]:
def compute_top_k_accuracy(image_paths, k=100):
    hits = 0
    num_batches = int(np.ceil(len(image_paths) / batch_size))
    for idx in tqdm(range(num_batches)):
        start_idx = idx * batch_size
        end_idx = start_idx + batch_size
        current_image_paths = image_paths[start_idx:end_idx]
        queries = [image_path_to_caption[image_path][0] for image_path in current_image_paths]
        result = find_matches(image_embeddings, queries, k)
        hits += sum([image_path in matches for (image_path, matches) in list(zip(current_image_paths, result))])

    return hits / len(image_paths)


print("Scoring training data...")
train_accuracy = compute_top_k_accuracy(train_image_paths)
print(f"Train accuracy: {round(train_accuracy * 100, 3)}%")

print("Scoring evaluation data...")
eval_accuracy = compute_top_k_accuracy(image_paths[train_size:])
print(f"Eval accuracy: {round(eval_accuracy * 100, 3)}%")

Scoring training data...


  0%|          | 0/118 [00:00<?, ?it/s]

100%|██████████| 118/118 [05:44<00:00,  2.92s/it]


Train accuracy: 0.9%
Scoring evaluation data...


100%|██████████| 35/35 [01:40<00:00,  2.87s/it]

Eval accuracy: 0.903%


## Final remarks

You can obtain better results by increasing the size of the training sample,
train for more epochs, explore other base encoders for images and text,
set the base encoders to be trainable, and tune the hyperparameters,
especially the `temperature` for the softmax in the loss computation.

Example available on HuggingFace

|                                                                         Trained Model                                                                          |                                                                                  Demo                                                                                  |
| :------------------------------------------------------------------------------------------------------------------------------------------------------------: | :--------------------------------------------------------------------------------------------------------------------------------------------------------------------: |
| [![Generic badge](https://img.shields.io/badge/%F0%9F%A4%97%20Model-nl%20image%20search-black.svg)](https://huggingface.co/keras-io/dual-encoder-image-search) | [![Generic badge](https://img.shields.io/badge/%F0%9F%A4%97%20Spaces-nl%20image%20search-black.svg)](https://huggingface.co/spaces/keras-io/dual-encoder-image-search) |
